#                                  Assigment 2
##                      Kalman Filter for object tracking

---


### Develop a Kalman filter to track a dual color ball through its movement over a video, even if its observed values are not correctly recognized.
---
#### ATENTION ####
_Due to Colab limitations with the Opencv library and other issues i choose to run my code externally in a virtual environment. And make this Colab as a means of documenting my work. All the codes are available in the git repo (https://github.com/gpizzigh-bit/Tracking-a-moving-ball)._

---

According to https://en.wikipedia.org/wiki/Kalman_filter [1] a Kalman filter is a real time optimal estimator algorithm capable of of estimating the values of an determined state over observed measurements,taking in to account inaccuracies and unknown variables.

The algorithm works in a two-phases process: the predict phase, where it uses a mathematical dynamic model to “predict” the future value of the state, and the “update” phase where it uses measurements obtained from different “sources”,  as sensors in a real-world scenarios or contours of binary masks on video frame, to update its guess value in the predict phase.               Both of these phases are susceptible to noise and uncertainty,  making the filter’s job to choose and weight a trust factor in each of its values in each epoch.









Basic_concept_of_Kalman_filtering.svg
<center>
Image 1 - Source: By Petteri Aimonen - Own work, CC0, https://commons.wikimedia.org/w/index.php?curid=17475883
</center>

The objective of this assignment is to develop a filter capable of estimating the trajectory of a moving dual color ball in a video even if its observed location wasn’t successfully obtained in each frame.

The first video which we will track is the video bellow: 

In [1]:
!git clone https://github.com/gpizzigh-bit/Tracking-a-moving-ball

Cloning into 'Tracking-a-moving-ball'...
remote: Enumerating objects: 64, done.
remote: Counting objects: 100% (64/64), done.
remote: Compressing objects: 100% (49/49), done.
remote: Total 64 (delta 22), reused 52 (delta 14), pack-reused 0
Unpacking objects: 100% (64/64), done.


In [2]:
from IPython.display import HTML, Image
from base64 import b64encode

mp4 = open('/content/Tracking-a-moving-ball/videos/sample1.mp4','rb').read()

data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=800 controls>
      <source src="%s" type="video/mp4">
</video>""" % data_url)

To successfully develop our filter, we need to first obtain the centroid of the ball in each frame. This will work as our observed and “measured” values for the filter and as “real" parameter for comparison. All of this code will be located in a file named find_obj.py, where I use a library called OpenCV to obtain the binary of each frame, which i will call mask, and filter it by color, to obtain a black and white binary mask and consequently find the location of the ball based on its colors. Bellow is the function present in the find_obj.py file that does that.

```
def find_object_inrange(video: str,scale: int):

    vc = cv.VideoCapture(video)

    mask_vec = []

    # order is B ,G, R 
    lower_color1_bounds = (65,65,0)
    upper_color1_bounds = (255,255,50)

    lower_color2_bounds = (60,0,170)
    upper_color2_bounds = (120,255,210)
    
    # Read until video is completed
    while(vc.isOpened()):

        ret, frame = vc.read()
        if ret == True:

            mask1 = cv.inRange(frame,lower_color1_bounds,upper_color1_bounds)
            mask2 = cv.inRange(frame,lower_color2_bounds,upper_color2_bounds)
            mask_final = mask1 | mask2
            mask_final = cv.resize(mask_final, (int(mask_final.shape[1]/scale),int(mask_final.shape[0]/scale)))
            mask_vec.append(mask_final)
        
    # Break the loop on the end of video
        else:
            break

    return mask_vec,len(mask_vec)
```

After "filtering" the ball from the rest of the video we can create a function that will obtain the countours and eventually the centroids of this white space
that represents the ball in our mask. Image [2] and [3] represent the function results.


<center>
<img src='https://github.com/gpizzigh-bit/Tracking-a-moving-ball/blob/main/images/mask_31.jpg?raw=tru'>

Image 2 - Binary mask of the ball, frame: 31.

<img src='https://github.com/gpizzigh-bit/Tracking-a-moving-ball/blob/main/images/mask_rgb_31.jpg?raw=tru'>

Image 3 - RGB mask of the ball, frame: 31.
</center>

The function that obteins the countours and centroids are located bellow.

```
def get_centroid_values(mask: classmethod, observation_px: list, observation_py: list):

    contours, _ = cv.findContours(mask, cv.RETR_EXTERNAL, cv.CHAIN_APPROX_NONE)

    if len(contours) <= 0: # error condition
        observation_px.append(-1)
        observation_py.append(-1) 

    #find largest contour   
    idx_max = contours[0]
    len_max = 0
    for c in contours:
        len_contour = len(c)
        if len_contour > len_max:
            len_max = len_contour
            idx_max = c
    M = cv.moments(idx_max)

    # If area of contour is zero => no detection possible
    if M['m00'] == 0 :
        observation_px.append(-1)
        observation_py.append(-1)
        cX = -1
        cY = -1
    else:
        # compute the center of the contour
        cX = int(M['m10']/M['m00'])
        cY = int(M['m01']/M['m00'])
        observation_px.append(cX)
        observation_py.append(cY)

    return cX, cY, observation_px, observation_py
```

To validate if we successfully obtained the centroid values, we can draw a circle in the x and y location values on the frame, we will call this “obs”.
<center>
<img src='https://github.com/gpizzigh-bit/Tracking-a-moving-ball/blob/main/images/frame_obs_31.jpg?raw=true'> 

Image 4 - Observed centroid value of frame 31.
</center>


These centroid values can be treated as our measured values for the filter because sometime in the video (around frames 38 to 40) the function above wasn’t able to get the balls’ position and so the filter should rely entirely on the prediction.

This prediction relies on a mathematical model given by the equations below, where x and y represent the x-axis pixel position and the y-axis pixel position, respectively, and k represent each epoch of our video.


$$
x_{k+1} = x_k + V_{x_k}t 
$$

$$
y_{k+1} = y_k + V_{y_k}t + g\frac{Δt^2}{2} 
$$

$$
V_{x_{k+1}} = \frac{V_{x_{k}} - V_{x_{k-1}}}{Δt}
$$

$$
V_{y_{k+1}} = \frac{V_{y_{k}} - V_{y_{k-1}}}{Δt}
$$

$$
Δt = \frac{1}{30}
$$

The catch her is the gravity value in the video in pixels who, I was able to obtain by measuring my core height and using an approximation of $10m/s^2$ which resulted in

$$
g = 3661 px/s^2
$$

Using these values, we can build the following Kalman filter matrices and vectors:

$$
  StateMatrix = \begin{bmatrix} 
	x_{k+1} \\
	y_{k+1} \\
	V_{x_{k+1}}  \\
  V_{y_{k+1}}  \\
	\end{bmatrix} 
$$

$$
	TransitionMatrix = \begin{bmatrix} 
	1 & 0 & Δt+g\frac{Δt^2}{2} & 0 \\
	0 & 1 & 0 & Δt+g\frac{Δt^2}{2} \\
	0 & 0 & 1 & 0 \\
  0 & 0 & 0 & 1 \\
	\end{bmatrix}
	\quad
$$

$$
	MeasurementMatrix = \begin{bmatrix} 
	1 & 0 & 0 & 0 \\
  0 & 1 & 0 & 0 \\
	\end{bmatrix}
	\quad
$$

$$
	ProcessNoiseCov = \begin{bmatrix} 
	1^{-2} & 0 & 0 & 0 \\
	0 & 1^{-2} & 0 & 0 \\
	0 & 0 & 1^{-2} & 0 \\
  0 & 0 & 0 & 1^{-2} \\
	\end{bmatrix}
	\quad
$$

$$
	MeasurementNoiseCov = \begin{bmatrix} 
	1^{-4} & 0  \\
	0 & 1^{-4} \\
	\end{bmatrix}
	\quad
$$

$$
	ErrorCovPost = \begin{bmatrix} 
	0.7 & 0 & 0 & 0 \\
	0 & 0.7 & 0 & 0 \\
	0 & 0 & 0.7 & 0 \\
  0 & 0 & 0 & 0.7 \\
	\end{bmatrix}
	\quad
$$

It’s important to point out that we could also get the velocities for the x and y axis in each epoch because all the matrices are built for a 4 variable state vector, but we choose to only measure the position as it is the most important values towards our goal. Having these equations, the next step is to build the filter, which I choose to build in a separate file named kf.py, it's code is shown below
 
```

import cv2 as cv
import numpy as np

def kalman_filter(cX:int, cY:int, dt: float, index: int, observation_px: list, observation_py: list):
    # initial values
    x_init = observation_px[0]
    y_init = observation_px[0]
    gravity_factor = int(((dt**2)/2) * 3661)
    vx_init = (observation_px[1]-observation_px[0])/dt
    vy_init = (observation_py[1]-observation_py[0])/dt
    init_state = [x_init, y_init, vx_init, vy_init]
    measured =[]
    measured_x = []
    measured_y = []
    predicted_px = [] 
    predicted_py = []
    mp = np.array((2,1), np.float32)
    tp = np.array((2,1), np.float32)


    param_state = 4  
    param_measured = 2

    kalman_filt = cv.KalmanFilter(param_state,param_measured)
    kalman_filt.statePost = np.array(init_state, np.float32)
    kalman_filt.statePre  = np.array(init_state, np.float32)

    # Matrix creation 
    kalman_filt.transitionMatrix = np.array([[1, 0, dt+gravity_factor, 0],
                                             [0, 1, 0, dt+gravity_factor],
                                             [0, 0, 1, 0],
                                             [0, 0, 0, 1]], np.float32) # F matrix

    kalman_filt.measurementMatrix = np.array([[1, 0 ,0 ,0],
                                              [0, 1, 0, 0]], np.float32) # H matrix

    kalman_filt.processNoiseCov = np.array([[1, 0 ,0 ,0],
                                              [0, 1, 0, 0],
                                              [0, 0, 1, 0],
                                              [0, 0, 0, 1]],np.float32) * 1e-2 # close to zero Q matrix
    
    kalman_filt.measurementNoiseCov = np.array([[1, 0],
                                                [0, 1]], np.float32) * 1e-4 # close to zero R matrix


    kalman_filt.errorCovPost = 0.7 * np.ones((4, 4))

    # range over all the observed values until now
    for i in range(1,index+1):
        if observation_px[i] > -1 and observation_py[i] > -1:
            mp[0] = observation_px[i] 
            mp[1] = observation_py[i]
            kalman_filt.correct(mp)
        else:
            mp[0] = 0
            mp[1] = 0

        measured.append(mp)
        measured_x.append((int(mp[0])))
        measured_y.append((int(mp[1])))

        tp = kalman_filt.predict()

        if (int(tp[0])) >= 0 and (int(tp[1])) >= 0:
            predicted_px.append((int(tp[0])))
            predicted_py.append((int(tp[1])))
        
        else:
            predicted_px.append(-1)
            predicted_py.append(-1)
    
    return len(measured), measured_x, measured_y, predicted_px, predicted_py

```

In this code, I make use of the built-in “KalmanFilter” function from the OpenCV library, which enables me to create the necessary matrices and the kalman equations are made inside the library. That makes it execute faster than making my own kalman equations, as these are python optimized. 

This is the resulting video output:

In [3]:

mp4 = open('/content/Tracking-a-moving-ball/videos/sample_1_out.mp4','rb').read()

data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=800 controls>
      <source src="%s" type="video/mp4">
</video>""" % data_url)

To better visualize the motion, the following graph was made on matplotlib

<center>
<img src='https://github.com/gpizzigh-bit/Tracking-a-moving-ball/blob/main/images/graph.png?raw=true'> 

Image 5 - Graphical plot of the ball location.
</center>

As you can see the filter performed amazingly tracking the balls location with precision as soon as i throw the ball in the air and it enters its parabolic motion which we mathematically model for the filter, even when the observed values could not be obtained the filter relied over the correct prediction and as soon as the measurements returned it made the necessary adjustments.

All the codes are available in the git repo (https://github.com/gpizzigh-bit/Tracking-a-moving-ball) just activate the virtual environment I created and run the main.py file. 